In [9]:
import pandas as pd
from os import listdir
from os.path import isfile, join
import numpy as np
from datetime import timedelta

In [17]:
# get data in desirved format
dow_files_addr = "./Data/Dow_30_1_min/"
etf_files_addr = "./Data/50_ETFs_1min/"

dow_files_names = [f for f in listdir(dow_files_addr)]
etf_files_names = [f for f in listdir(etf_files_addr)]

dow_names = [f.split(".")[0] for f in dow_files_names]
etf_names = [f.split(".")[0] for f in etf_files_names]

dow_dfs = []
etf_dfs = []
headers = ["date", "time", "open_price", "close_price", "highest_price", "lowest_price", "volumn"]
dtypes={"date": "str", 
    "time":"str",
    "open_price": "float", 
    "highest_price": "float",
    "lowest_price": "float", 
    "close_price": "float",
    "volumn": "int"}

def read_files(files_names, files_addr):
    dfs = []
    for name in files_names:
        df = pd.read_csv(files_addr + name, sep=",",names=headers,dtype=dtypes, header=None)
        df["datetime"] = df["date"] + " " + df["time"]
        df["datetime"] = pd.to_datetime(df["datetime"], format="%m/%d/%Y %H:%M")
        df["hour"] = df["time"].str.split(":", expand=True)[0].astype(int)
        df["minute"] = df["time"].str.split(":", expand=True)[1].astype(int)
        df = df.sort_values(by=["datetime"])
        df = df.drop(columns=["date"])
        df = df.drop(columns=["time"])
        dfs.append(df)
    return dfs

print("Start read dow file...")
dow_dfs = read_files(dow_files_names, dow_files_addr)
# for dow_name in dow_files_names:
#     df = pd.read_csv(dow_files_addr + dow_name, sep=",",names=headers,dtype=dtypes, header=None)
#     df["datetime"] = df["date"] + " " + df["time"]
#     df["datetime"] = pd.to_datetime(df["datetime"], format="%m/%d/%Y %H:%M")
#     df["hour"] = df["time"].str.split(":", expand=True)[0].astype(int)
#     df["minute"] = df["time"].str.split(":", expand=True)[1].astype(int)
#     df = df.sort_values(by=["datetime"])
#     df = df.drop(columns=["date"])
#     df = df.drop(columns=["time"])
#     dow_dfs.append(df)
print("Finish read dow file.")
print("---------------------")
print("Start read etf file...")
etf_dfs = read_files(etf_files_names, etf_files_addr)
# for etf_name in etf_files_names:
#     df = pd.read_csv(etf_files_addr + etf_name, sep=",",names=headers,dtype=dtypes, header=None)
#     df["datetime"] = df["date"] + " " + df["time"]
#     df["datetime"] = pd.to_datetime(df["datetime"], format="%m/%d/%Y %H:%M")
#     df["hour"] = df["time"].str.split(":", expand=True)[0].astype(int)
#     df["minute"] = df["time"].str.split(":", expand=True)[1].astype(int)
#     df = df.sort_values(by=["datetime"])
#     df = df.drop(columns=["date"])
#     df = df.drop(columns=["time"])
#     etf_dfs.append(df)
print("Finish read etf file.")

Start read dow file...
Finish read dow file.
---------------------
Start read etf file...
Finish read etf file.


In [31]:
# get start and end for both dow and etf that cove evey df

dow_time_slice = [min(dow_dfs[0]["datetime"]), max(dow_dfs[0]["datetime"])]
etf_time_slice = [min(etf_dfs[0]["datetime"]), max(etf_dfs[0]["datetime"])]

def find_common_time_slice(dfs, time_slice, files_names):
    i = 0
    for df in dfs:
        start = min(df["datetime"])
        if start > time_slice[0]:
            print("start", files_names[i])
            print(start)
            time_slice[0] = start
        end = max(df["datetime"])
        if end < time_slice[1]:
            print("end", files_names[i])
            print(end)
            time_slice[1] = end
        i += 1
    return time_slice

print("Start check dow date...")
dow_time_slice = find_common_time_slice(dow_dfs, dow_time_slice, dow_files_names)
# for df in dow_dfs:
#     start = min(df["datetime"])
#     if start > dow_time_slice[0]:
#         print("start", dow_files_names[i])
#         print(start)
#         dow_time_slice[0] = start
#     end = max(df["datetime"])
#     if end < dow_time_slice[1]:
#         print("end", dow_files_names[i])
#         print(end)
#         dow_time_slice[1] = end
print("Finish check dow date...")
print("---------------------")
print("Start check etf date...")
etf_time_slice = find_common_time_slice(etf_dfs, etf_time_slice, etf_files_names)
# for df in etf_dfs:
#     start = min(df["datetime"])
#     if start > etf_time_slice[0]:
#         print("start", dow_files_names[i])
#         print(start)
#         etf_time_slice[0] = start
#     end = max(df["datetime"])
#     if end < etf_time_slice[1]:
#         print("end", dow_files_names[i])
#         print(end)
#         etf_time_slice[1] = end
print("Finish check etf date...")

Start check dow date...
start GM.txt
2010-11-18 09:36:00
Finish check dow date...
---------------------
Start check etf date...
start ERX.txt
2008-11-19 09:30:00
start UPRO.txt
2009-06-25 09:40:00
Finish check etf date...


In [71]:
dow_time_slice

[Timestamp('2010-11-18 09:36:00'), Timestamp('2020-06-05 15:48:00')]

In [33]:
etf_time_slice

[Timestamp('2009-06-25 09:40:00'), Timestamp('2020-06-05 16:00:00')]

In [34]:
# limit all of the df to the same time frames
for i in range(len(dow_dfs)):
    dow_dfs[i] = dow_dfs[i].loc[(dow_dfs[i]["datetime"] >= dow_time_slice[0]) & (dow_dfs[i]["datetime"] <= dow_time_slice[1])]
for i in range(len(etf_dfs)):
    etf_dfs[i] = etf_dfs[i].loc[(etf_dfs[i]["datetime"] >= etf_time_slice[0]) & (etf_dfs[i]["datetime"] <= etf_time_slice[1])]

In [126]:
# make the time inteval 5 min and uniform

def modify_time_inteval(dfs, time_slice, time_inteval):
    for i in range(len(dfs)):
        cur_open_price = dfs[i].iloc[0]["open_price"]
        cur_close_price = dfs[i].iloc[0]["close_price"]
        cur_highest_price = dfs[i].iloc[0]["highest_price"]  
        cur_lowest_price = dfs[i].iloc[0]["lowest_price"]
        # cur_volumn = dfs[i].iloc[0]["volumn"]
        
        start_time = time_slice[0]
        end_time = time_slice[1]
        cur_time = (start_time + timedelta(days=1)).replace(hour=9, minute=30)
        target_time =  start_time
        
        headers = ["open_price", "close_price", "highest_price", "lowest_price", "volumn", "datetime", "hour", "minute"]
        df = pd.DataFrame(columns=headers)
        ndfs = []
        ###############################
        print(i)
        ###############################
        row_num = dfs[i].shape[0]
        j = 0
        while cur_time < end_time:
            print(cur_time)
            while target_time < cur_time and j < row_num:
                k = j - 1
                if dfs[i].iloc[j]["datetime"] > cur_time:
                    target_time = dfs[i].iloc[j]["datetime"]
                    cur_open_price = dfs[i].iloc[k]["open_price"]
                    cur_close_price = dfs[i].iloc[k]["close_price"]
                    cur_highest_price = dfs[i].iloc[k]["highest_price"]
                    cur_lowest_price = dfs[i].iloc[k]["lowest_price"]   
                j += 1

            df= df.append(pd.DataFrame(np.array([[cur_open_price, cur_close_price, cur_highest_price, cur_lowest_price, 0, cur_time,
                                            cur_time.to_pydatetime().hour, cur_time.to_pydatetime().minute]]),
                                columns=headers), ignore_index=True)
            # update time
            cur_time += timedelta(minutes=5)
            if cur_time.to_pydatetime().hour >= 16 and cur_time.to_pydatetime().minute != 0:
                cur_time += timedelta(days=1)
                cur_time =  cur_time.replace(hour=9, minute=30)
        ndfs.append(df)
    return ndfs

In [128]:
a = modify_time_inteval([tmp], dow_time_slice, 5)[0]

0
2010-11-19 09:30:00
2010-11-19 09:35:00
2010-11-19 09:40:00
2010-11-19 09:45:00
2010-11-19 09:50:00
2010-11-19 09:55:00
2010-11-19 10:00:00
2010-11-19 10:05:00
2010-11-19 10:10:00
2010-11-19 10:15:00
2010-11-19 10:20:00
2010-11-19 10:25:00
2010-11-19 10:30:00
2010-11-19 10:35:00
2010-11-19 10:40:00
2010-11-19 10:45:00
2010-11-19 10:50:00
2010-11-19 10:55:00
2010-11-19 11:00:00
2010-11-19 11:05:00
2010-11-19 11:10:00
2010-11-19 11:15:00
2010-11-19 11:20:00
2010-11-19 11:25:00
2010-11-19 11:30:00
2010-11-19 11:35:00
2010-11-19 11:40:00
2010-11-19 11:45:00
2010-11-19 11:50:00
2010-11-19 11:55:00
2010-11-19 12:00:00
2010-11-19 12:05:00
2010-11-19 12:10:00
2010-11-19 12:15:00
2010-11-19 12:20:00
2010-11-19 12:25:00
2010-11-19 12:30:00
2010-11-19 12:35:00
2010-11-19 12:40:00
2010-11-19 12:45:00
2010-11-19 12:50:00
2010-11-19 12:55:00
2010-11-19 13:00:00
2010-11-19 13:05:00
2010-11-19 13:10:00
2010-11-19 13:15:00
2010-11-19 13:20:00
2010-11-19 13:25:00
2010-11-19 13:30:00
2010-11-19 13:35:0

2010-11-24 12:05:00
2010-11-24 12:10:00
2010-11-24 12:15:00
2010-11-24 12:20:00
2010-11-24 12:25:00
2010-11-24 12:30:00
2010-11-24 12:35:00
2010-11-24 12:40:00
2010-11-24 12:45:00
2010-11-24 12:50:00
2010-11-24 12:55:00
2010-11-24 13:00:00
2010-11-24 13:05:00
2010-11-24 13:10:00
2010-11-24 13:15:00
2010-11-24 13:20:00
2010-11-24 13:25:00
2010-11-24 13:30:00
2010-11-24 13:35:00
2010-11-24 13:40:00
2010-11-24 13:45:00
2010-11-24 13:50:00
2010-11-24 13:55:00
2010-11-24 14:00:00
2010-11-24 14:05:00
2010-11-24 14:10:00
2010-11-24 14:15:00
2010-11-24 14:20:00
2010-11-24 14:25:00
2010-11-24 14:30:00
2010-11-24 14:35:00
2010-11-24 14:40:00
2010-11-24 14:45:00
2010-11-24 14:50:00
2010-11-24 14:55:00
2010-11-24 15:00:00
2010-11-24 15:05:00
2010-11-24 15:10:00
2010-11-24 15:15:00
2010-11-24 15:20:00
2010-11-24 15:25:00
2010-11-24 15:30:00
2010-11-24 15:35:00
2010-11-24 15:40:00
2010-11-24 15:45:00
2010-11-24 15:50:00
2010-11-24 15:55:00
2010-11-24 16:00:00
2010-11-25 09:30:00
2010-11-25 09:35:00


2010-11-29 15:50:00
2010-11-29 15:55:00
2010-11-29 16:00:00
2010-11-30 09:30:00
2010-11-30 09:35:00
2010-11-30 09:40:00
2010-11-30 09:45:00
2010-11-30 09:50:00
2010-11-30 09:55:00
2010-11-30 10:00:00
2010-11-30 10:05:00
2010-11-30 10:10:00
2010-11-30 10:15:00
2010-11-30 10:20:00
2010-11-30 10:25:00
2010-11-30 10:30:00
2010-11-30 10:35:00
2010-11-30 10:40:00
2010-11-30 10:45:00
2010-11-30 10:50:00
2010-11-30 10:55:00
2010-11-30 11:00:00
2010-11-30 11:05:00
2010-11-30 11:10:00
2010-11-30 11:15:00
2010-11-30 11:20:00
2010-11-30 11:25:00
2010-11-30 11:30:00
2010-11-30 11:35:00
2010-11-30 11:40:00
2010-11-30 11:45:00
2010-11-30 11:50:00
2010-11-30 11:55:00
2010-11-30 12:00:00
2010-11-30 12:05:00
2010-11-30 12:10:00
2010-11-30 12:15:00
2010-11-30 12:20:00
2010-11-30 12:25:00
2010-11-30 12:30:00
2010-11-30 12:35:00
2010-11-30 12:40:00
2010-11-30 12:45:00
2010-11-30 12:50:00
2010-11-30 12:55:00
2010-11-30 13:00:00
2010-11-30 13:05:00
2010-11-30 13:10:00
2010-11-30 13:15:00
2010-11-30 13:20:00


2010-12-05 14:00:00
2010-12-05 14:05:00
2010-12-05 14:10:00
2010-12-05 14:15:00
2010-12-05 14:20:00
2010-12-05 14:25:00
2010-12-05 14:30:00
2010-12-05 14:35:00
2010-12-05 14:40:00
2010-12-05 14:45:00
2010-12-05 14:50:00
2010-12-05 14:55:00
2010-12-05 15:00:00
2010-12-05 15:05:00
2010-12-05 15:10:00
2010-12-05 15:15:00
2010-12-05 15:20:00
2010-12-05 15:25:00
2010-12-05 15:30:00
2010-12-05 15:35:00
2010-12-05 15:40:00
2010-12-05 15:45:00
2010-12-05 15:50:00
2010-12-05 15:55:00
2010-12-05 16:00:00
2010-12-06 09:30:00
2010-12-06 09:35:00
2010-12-06 09:40:00
2010-12-06 09:45:00
2010-12-06 09:50:00
2010-12-06 09:55:00
2010-12-06 10:00:00
2010-12-06 10:05:00
2010-12-06 10:10:00
2010-12-06 10:15:00
2010-12-06 10:20:00
2010-12-06 10:25:00
2010-12-06 10:30:00
2010-12-06 10:35:00
2010-12-06 10:40:00
2010-12-06 10:45:00
2010-12-06 10:50:00
2010-12-06 10:55:00
2010-12-06 11:00:00
2010-12-06 11:05:00
2010-12-06 11:10:00
2010-12-06 11:15:00
2010-12-06 11:20:00
2010-12-06 11:25:00
2010-12-06 11:30:00


2010-12-11 11:45:00
2010-12-11 11:50:00
2010-12-11 11:55:00
2010-12-11 12:00:00
2010-12-11 12:05:00
2010-12-11 12:10:00
2010-12-11 12:15:00
2010-12-11 12:20:00
2010-12-11 12:25:00
2010-12-11 12:30:00
2010-12-11 12:35:00
2010-12-11 12:40:00
2010-12-11 12:45:00
2010-12-11 12:50:00
2010-12-11 12:55:00
2010-12-11 13:00:00
2010-12-11 13:05:00
2010-12-11 13:10:00
2010-12-11 13:15:00
2010-12-11 13:20:00
2010-12-11 13:25:00
2010-12-11 13:30:00
2010-12-11 13:35:00
2010-12-11 13:40:00
2010-12-11 13:45:00
2010-12-11 13:50:00
2010-12-11 13:55:00
2010-12-11 14:00:00
2010-12-11 14:05:00
2010-12-11 14:10:00
2010-12-11 14:15:00
2010-12-11 14:20:00
2010-12-11 14:25:00
2010-12-11 14:30:00
2010-12-11 14:35:00
2010-12-11 14:40:00
2010-12-11 14:45:00
2010-12-11 14:50:00
2010-12-11 14:55:00
2010-12-11 15:00:00
2010-12-11 15:05:00
2010-12-11 15:10:00
2010-12-11 15:15:00
2010-12-11 15:20:00
2010-12-11 15:25:00
2010-12-11 15:30:00
2010-12-11 15:35:00
2010-12-11 15:40:00
2010-12-11 15:45:00
2010-12-11 15:50:00


...

2020-05-13 11:25:00
2020-05-13 11:30:00
2020-05-13 11:35:00
2020-05-13 11:40:00
2020-05-13 11:45:00
2020-05-13 11:50:00
2020-05-13 11:55:00
2020-05-13 12:00:00
2020-05-13 12:05:00
2020-05-13 12:10:00
2020-05-13 12:15:00
2020-05-13 12:20:00
2020-05-13 12:25:00
2020-05-13 12:30:00
2020-05-13 12:35:00
2020-05-13 12:40:00
2020-05-13 12:45:00
2020-05-13 12:50:00
2020-05-13 12:55:00
2020-05-13 13:00:00
2020-05-13 13:05:00
2020-05-13 13:10:00
2020-05-13 13:15:00
2020-05-13 13:20:00
2020-05-13 13:25:00
2020-05-13 13:30:00
2020-05-13 13:35:00
2020-05-13 13:40:00
2020-05-13 13:45:00
2020-05-13 13:50:00
2020-05-13 13:55:00
2020-05-13 14:00:00
2020-05-13 14:05:00
2020-05-13 14:10:00
2020-05-13 14:15:00
2020-05-13 14:20:00
2020-05-13 14:25:00
2020-05-13 14:30:00
2020-05-13 14:35:00
2020-05-13 14:40:00
2020-05-13 14:45:00
2020-05-13 14:50:00
2020-05-13 14:55:00
2020-05-13 15:00:00
2020-05-13 15:05:00
2020-05-13 15:10:00
2020-05-13 15:15:00
2020-05-13 15:20:00
2020-05-13 15:25:00
2020-05-13 15:30:00


2020-05-18 12:45:00
2020-05-18 12:50:00
2020-05-18 12:55:00
2020-05-18 13:00:00
2020-05-18 13:05:00
2020-05-18 13:10:00
2020-05-18 13:15:00
2020-05-18 13:20:00
2020-05-18 13:25:00
2020-05-18 13:30:00
2020-05-18 13:35:00
2020-05-18 13:40:00
2020-05-18 13:45:00
2020-05-18 13:50:00
2020-05-18 13:55:00
2020-05-18 14:00:00
2020-05-18 14:05:00
2020-05-18 14:10:00
2020-05-18 14:15:00
2020-05-18 14:20:00
2020-05-18 14:25:00
2020-05-18 14:30:00
2020-05-18 14:35:00
2020-05-18 14:40:00
2020-05-18 14:45:00
2020-05-18 14:50:00
2020-05-18 14:55:00
2020-05-18 15:00:00
2020-05-18 15:05:00
2020-05-18 15:10:00
2020-05-18 15:15:00
2020-05-18 15:20:00
2020-05-18 15:25:00
2020-05-18 15:30:00
2020-05-18 15:35:00
2020-05-18 15:40:00
2020-05-18 15:45:00
2020-05-18 15:50:00
2020-05-18 15:55:00
2020-05-18 16:00:00
2020-05-19 09:30:00
2020-05-19 09:35:00
2020-05-19 09:40:00
2020-05-19 09:45:00
2020-05-19 09:50:00
2020-05-19 09:55:00
2020-05-19 10:00:00
2020-05-19 10:05:00
2020-05-19 10:10:00
2020-05-19 10:15:00


2020-05-23 14:00:00
2020-05-23 14:05:00
2020-05-23 14:10:00
2020-05-23 14:15:00
2020-05-23 14:20:00
2020-05-23 14:25:00
2020-05-23 14:30:00
2020-05-23 14:35:00
2020-05-23 14:40:00
2020-05-23 14:45:00
2020-05-23 14:50:00
2020-05-23 14:55:00
2020-05-23 15:00:00
2020-05-23 15:05:00
2020-05-23 15:10:00
2020-05-23 15:15:00
2020-05-23 15:20:00
2020-05-23 15:25:00
2020-05-23 15:30:00
2020-05-23 15:35:00
2020-05-23 15:40:00
2020-05-23 15:45:00
2020-05-23 15:50:00
2020-05-23 15:55:00
2020-05-23 16:00:00
2020-05-24 09:30:00
2020-05-24 09:35:00
2020-05-24 09:40:00
2020-05-24 09:45:00
2020-05-24 09:50:00
2020-05-24 09:55:00
2020-05-24 10:00:00
2020-05-24 10:05:00
2020-05-24 10:10:00
2020-05-24 10:15:00
2020-05-24 10:20:00
2020-05-24 10:25:00
2020-05-24 10:30:00
2020-05-24 10:35:00
2020-05-24 10:40:00
2020-05-24 10:45:00
2020-05-24 10:50:00
2020-05-24 10:55:00
2020-05-24 11:00:00
2020-05-24 11:05:00
2020-05-24 11:10:00
2020-05-24 11:15:00
2020-05-24 11:20:00
2020-05-24 11:25:00
2020-05-24 11:30:00


2020-05-28 15:20:00
2020-05-28 15:25:00
2020-05-28 15:30:00
2020-05-28 15:35:00
2020-05-28 15:40:00
2020-05-28 15:45:00
2020-05-28 15:50:00
2020-05-28 15:55:00
2020-05-28 16:00:00
2020-05-29 09:30:00
2020-05-29 09:35:00
2020-05-29 09:40:00
2020-05-29 09:45:00
2020-05-29 09:50:00
2020-05-29 09:55:00
2020-05-29 10:00:00
2020-05-29 10:05:00
2020-05-29 10:10:00
2020-05-29 10:15:00
2020-05-29 10:20:00
2020-05-29 10:25:00
2020-05-29 10:30:00
2020-05-29 10:35:00
2020-05-29 10:40:00
2020-05-29 10:45:00
2020-05-29 10:50:00
2020-05-29 10:55:00
2020-05-29 11:00:00
2020-05-29 11:05:00
2020-05-29 11:10:00
2020-05-29 11:15:00
2020-05-29 11:20:00
2020-05-29 11:25:00
2020-05-29 11:30:00
2020-05-29 11:35:00
2020-05-29 11:40:00
2020-05-29 11:45:00
2020-05-29 11:50:00
2020-05-29 11:55:00
2020-05-29 12:00:00
2020-05-29 12:05:00
2020-05-29 12:10:00
2020-05-29 12:15:00
2020-05-29 12:20:00
2020-05-29 12:25:00
2020-05-29 12:30:00
2020-05-29 12:35:00
2020-05-29 12:40:00
2020-05-29 12:45:00
2020-05-29 12:50:00


2020-06-03 10:00:00
2020-06-03 10:05:00
2020-06-03 10:10:00
2020-06-03 10:15:00
2020-06-03 10:20:00
2020-06-03 10:25:00
2020-06-03 10:30:00
2020-06-03 10:35:00
2020-06-03 10:40:00
2020-06-03 10:45:00
2020-06-03 10:50:00
2020-06-03 10:55:00
2020-06-03 11:00:00
2020-06-03 11:05:00
2020-06-03 11:10:00
2020-06-03 11:15:00
2020-06-03 11:20:00
2020-06-03 11:25:00
2020-06-03 11:30:00
2020-06-03 11:35:00
2020-06-03 11:40:00
2020-06-03 11:45:00
2020-06-03 11:50:00
2020-06-03 11:55:00
2020-06-03 12:00:00
2020-06-03 12:05:00
2020-06-03 12:10:00
2020-06-03 12:15:00
2020-06-03 12:20:00
2020-06-03 12:25:00
2020-06-03 12:30:00
2020-06-03 12:35:00
2020-06-03 12:40:00
2020-06-03 12:45:00
2020-06-03 12:50:00
2020-06-03 12:55:00
2020-06-03 13:00:00
2020-06-03 13:05:00
2020-06-03 13:10:00
2020-06-03 13:15:00
2020-06-03 13:20:00
2020-06-03 13:25:00
2020-06-03 13:30:00
2020-06-03 13:35:00
2020-06-03 13:40:00
2020-06-03 13:45:00
2020-06-03 13:50:00
2020-06-03 13:55:00
2020-06-03 14:00:00
2020-06-03 14:05:00


In [129]:
a.shape

(275470, 8)

In [131]:
a

open_price close_price highest_price lowest_price volumn  \
0           29.87        29.9         29.85        29.85      0   
1           29.87        29.9         29.85        29.85      0   
2           29.87        29.9         29.85        29.85      0   
3           29.87        29.9         29.85        29.85      0   
4           29.87        29.9         29.85        29.85      0   
...           ...         ...           ...          ...    ...   
275465      29.87        29.9         29.85        29.85      0   
275466      29.87        29.9         29.85        29.85      0   
275467      29.87        29.9         29.85        29.85      0   
275468      29.87        29.9         29.85        29.85      0   
275469      29.87        29.9         29.85        29.85      0   

                  datetime hour minute  
0      2010-11-19 09:30:00    9     30  
1      2010-11-19 09:35:00    9     35  
2      2010-11-19 09:40:00    9     40  
3      2010-11-19 09:45:00    9     45  
4      2010-11-19 09:50:00    9     50  
...                    ...  ...    ...  
275465 2020-06-05 15:25:00   15     25  
275466 2020-06-05 15:30:00   15     30  
275467 2020-06-05 15:35:00   15     35  
275468 2020-06-05 15:40:00   15     40  
275469 2020-06-05 15:45:00   15     45  

[275470 rows x 8 columns]

In [63]:
tmp = dow_dfs[0].iloc[2:4]

In [119]:
tmp

open_price  close_price  highest_price  lowest_price  volumn  \
418029       29.87         29.9          29.85         29.85   13885   
418030       29.87         29.9          29.81         29.83   39934   

                  datetime  hour  minute  
418029 2010-11-18 09:38:00     9      38  
418030 2010-11-18 09:39:00     9      39

In [120]:
modify_time_inteval([tmp], dow_time_slice, 5)[0]

0


UnboundLocalError: local variable 'target_time' referenced before assignment

In [66]:
new_temp[0]

open_price close_price highest_price lowest_price volumn  \
0          29.87        29.9         29.85        29.85      0   
1          29.87        29.9         29.85        29.85      0   
2          29.87        29.9         29.85        29.85  13885   
3          29.87        29.9         29.81        29.83  39934   
4          29.87        29.9         29.85        29.83      0   
...          ...         ...           ...          ...    ...   
20950      29.87        29.9         29.85        29.83      0   
20951      29.87        29.9         29.85        29.83      0   
20952      29.87        29.9         29.85        29.83      0   
20953      29.87        29.9         29.85        29.83      0   
20954      29.87        29.9         29.85        29.83      0   

                 datetime hour minute  
0     2010-11-18 09:36:00    9     36  
1     2010-11-18 09:37:00    9     37  
2     2010-11-18 09:38:00    9     38  
3     2010-11-18 09:39:00    9     39  
4     2010-11-18 09:40:00    9     40  
...                   ...  ...    ...  
20950 2020-05-31 22:46:00   22     46  
20951 2020-06-01 22:47:00   22     47  
20952 2020-06-02 22:48:00   22     48  
20953 2020-06-03 22:49:00   22     49  
20954 2020-06-04 22:50:00   22     50  

[20955 rows x 8 columns]

In [44]:
cur_open_price = tmp.iloc[0]["open_price"]
cur_close_price = tmp.iloc[0]["close_price"]
cur_highest_price = tmp.iloc[0]["highest_price"]  
cur_lowest_price = tmp.iloc[0]["lowest_price"]
# cur_volumn = tmp.iloc[0]["volumn"]

start_time = dow_time_slice[0]
end_time = dow_time_slice[1]
cur_time = start_time

headers = ["open_price", "close_price", "highest_price", "lowest_price", "volumn", "datetime", "hour", "minute"]
df = pd.DataFrame(columns=headers)
for _ in range(100):
    print(cur_time)
    # if exist
    if cur_time in pd.DatetimeIndex(tmp["datetime"]):
        j = pd.DatetimeIndex(tmp["datetime"]).to_numpy().tolist().index(cur_time.to_numpy().tolist())
        df = df.append(tmp.iloc[j], ignore_index=True)
        cur_open_price = tmp.iloc[j]["open_price"]
        cur_close_price = tmp.iloc[j]["close_price"]    
        cur_lowest_price = tmp.iloc[j]["lowest_price"]
        # cur_volumn = tmp.iloc[j]["volumn"]
    # if not exist
    else:
        df= df.append(pd.DataFrame(np.array([[cur_open_price, cur_close_price, cur_highest_price, cur_lowest_price, 0, 
                                              cur_time, cur_time.to_pydatetime().hour, cur_time.to_pydatetime().minute]]),
                                  columns=headers), ignore_index=True)
    # update time
    cur_time += timedelta(minutes=1)
    if cur_time.to_pydatetime().hour >= 20 and cur_time.to_pydatetime().minute != 0:
        cur_time += timedelta(days=1)
        cur_time.replace(hour=9, minute=0)
    


2010-11-18 09:36:00
2010-11-18 09:37:00
2010-11-18 09:38:00
2010-11-18 09:39:00
2010-11-18 09:40:00
2010-11-18 09:41:00
2010-11-18 09:42:00
2010-11-18 09:43:00
2010-11-18 09:44:00
2010-11-18 09:45:00
2010-11-18 09:46:00
2010-11-18 09:47:00
2010-11-18 09:48:00
2010-11-18 09:49:00
2010-11-18 09:50:00
2010-11-18 09:51:00
2010-11-18 09:52:00
2010-11-18 09:53:00
2010-11-18 09:54:00
2010-11-18 09:55:00
2010-11-18 09:56:00
2010-11-18 09:57:00
2010-11-18 09:58:00
2010-11-18 09:59:00
2010-11-18 10:00:00
2010-11-18 10:01:00
2010-11-18 10:02:00
2010-11-18 10:03:00
2010-11-18 10:04:00
2010-11-18 10:05:00
2010-11-18 10:06:00
2010-11-18 10:07:00
2010-11-18 10:08:00
2010-11-18 10:09:00
2010-11-18 10:10:00
2010-11-18 10:11:00
2010-11-18 10:12:00
2010-11-18 10:13:00
2010-11-18 10:14:00
2010-11-18 10:15:00
2010-11-18 10:16:00
2010-11-18 10:17:00
2010-11-18 10:18:00
2010-11-18 10:19:00
2010-11-18 10:20:00
2010-11-18 10:21:00
2010-11-18 10:22:00
2010-11-18 10:23:00
2010-11-18 10:24:00
2010-11-18 10:25:00


In [61]:
tmp

open_price  close_price  highest_price  lowest_price  volumn  \
418029       29.87         29.9          29.85         29.85   13885   
418030       29.87         29.9          29.81         29.83   39934   

                  datetime  hour  minute  
418029 2010-11-18 09:38:00     9      38  
418030 2010-11-18 09:39:00     9      39